In [1]:


import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)



i

/kaggle/input/airline-reviews/Airline_review.csv


In [2]:
df=pd.read_csv("/kaggle/input/airline-reviews/Airline_review.csv")

In [4]:
pd.set_option('display.max_columns',None)
df.head(3)

/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1458: RuntimeWarning: invalid value encountered in greater
  has_large_values = (abs_vals > 1e6).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in less
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in greater
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()


Unnamed: 0 Airline Name Overall_Rating                    Review_Title  \
0           0  AB Aviation              9         "pretty decent airline"   
1           1  AB Aviation              1            "Not a good airline"   
2           2  AB Aviation              1  "flight was fortunately short"   

          Review Date  Verified  \
0  11th November 2019      True   
1      25th June 2019      True   
2      25th June 2019      True   

                                              Review       Aircraft  \
0    Moroni to Moheli. Turned out to be a pretty ...            NaN   
1   Moroni to Anjouan. It is a very small airline...           E120   
2    Anjouan to Dzaoudzi. A very small airline an...  Embraer E120    

  Type Of Traveller      Seat Type                Route     Date Flown  \
0      Solo Leisure  Economy Class     Moroni to Moheli  November 2019   
1      Solo Leisure  Economy Class    Moroni to Anjouan      June 2019   
2      Solo Leisure  Economy Class  Anjouan to Dzaoudzi      June 2019   

   Seat Comfort  Cabin Staff Service  Food & Beverages  Ground Service  \
0           4.0                  5.0               4.0             4.0   
1           2.0                  2.0               1.0             1.0   
2           2.0                  1.0               1.0             1.0   

   Inflight Entertainment  Wifi & Connectivity  Value For Money Recommended  
0                     NaN                  NaN              3.0         yes  
1                     NaN                  NaN              2.0          no  
2                     NaN                  NaN              2.0          no

In [5]:
from ydata_profiling import ProfileReport
profil = ProfileReport(df, title="Pandas Profiling Report")
profil

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [26]:
df1=df[["Review","Recommended"]]
df1["Recommended"] = df1["Recommended"].map({"yes": 1, "no": 0})


<ipython-input-26-b698263f1804>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1["Recommended"] = df1["Recommended"].map({"yes": 1, "no": 0})


In [27]:
df1.isna().sum()

Review         0
Recommended    0
dtype: int64

In [29]:
# Most ratings are negative
df1['Recommended'].mean()

0.33692978291830306

In [ ]:
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
import nltk
import re
import string



lemmatizer = WordNetLemmatizer()
stop_words = set(stopwords.words("english"))

def clean_text(text):
    
    text = text.lower()
    text = re.sub(f"[{string.punctuation}]", " ", text)  
    text = re.sub(r"\s+", " ", text).strip()  
    return text

def lemmatize_text(text):
    
    words = word_tokenize(text)  
    lemmatized_text = " ".join([lemmatizer.lemmatize(word) for word in words if word not in stop_words])
    return lemmatized_text

df1['Review'] = [clean_text(text) for text in df1['Review']]



In [31]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(df1['Review'], 
                                                    df1['Recommended'], 
                                                    random_state=0)

In [39]:
from sklearn.feature_extraction.text import CountVectorizer

vect = CountVectorizer().fit(X_train)
len(vect.get_feature_names_out())

29828

In [41]:
X_train_vectorized = vect.transform(X_train)

X_train_vectorized

<17378x29828 sparse matrix of type '<class 'numpy.int64'>'
	with 1415397 stored elements in Compressed Sparse Row format>

In [54]:
from sklearn.linear_model import LogisticRegression

# Train the model
model = LogisticRegression()
model.fit(X_train_vectorized, y_train)

/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


LogisticRegression()

In [55]:
from sklearn.metrics import roc_auc_score

# Predict the transformed test documents
predictions = model.predict(vect.transform(X_test))

print('AUC: ', roc_auc_score(y_test, predictions))

AUC:  0.8768855968079926


TFidf

In [62]:

from sklearn.feature_extraction.text import TfidfVectorizer

# Fit the TfidfVectorizer to the training data specifiying a minimum document frequency of 5
vect = TfidfVectorizer(min_df=5).fit(X_train)

In [63]:
X_train_vectorized = vect.transform(X_train)

model = LogisticRegression()
model.fit(X_train_vectorized, y_train)

predictions = model.predict(vect.transform(X_test))

print('AUC: ', roc_auc_score(y_test, predictions))

AUC:  0.8827137750566221


In [85]:
vect = CountVectorizer(min_df=5, ngram_range=(1,3)).fit(X_train)

X_train_vectorized = vect.transform(X_train)
model = LogisticRegression()
model.fit(X_train_vectorized, y_train)

predictions = model.predict(vect.transform(X_test))

print('AUC: ', roc_auc_score(y_test, predictions))


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


AUC:  0.8921998364837118


In [87]:
import xgboost as xgb

xgb_cl = xgb.XGBClassifier(eval_metric='mlogloss')
xgb_cl.fit(X_train_vectorized, y_train)
predictions = xgb_cl.predict(vect.transform(X_test))
print('AUC: ', roc_auc_score(y_test, predictions))


AUC:  0.8785576699193531


In [91]:
from sklearn.neural_network import MLPClassifier
clf = MLPClassifier(hidden_layer_sizes = [100, 100], alpha = 5.0,
                   random_state = 0, solver='lbfgs').fit(X_train_vectorized, y_train)


predictions = clf.predict(vect.transform(X_test))
print('AUC: ', roc_auc_score(y_test, predictions))


/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:541: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)


AUC:  0.8885126500222255
